In [1]:
# Import packages
library(rstan)
library(coda)
library(parallel)
library(Bessel)

Loading required package: StanHeaders
Loading required package: ggplot2
Registered S3 methods overwritten by 'ggplot2':
  method         from 
  [.quosures     rlang
  c.quosures     rlang
  print.quosures rlang
rstan (Version 2.19.2, GitRev: 2e1f913d3ca3)
For execution on a local, multicore CPU with excess RAM we recommend calling
options(mc.cores = parallel::detectCores()).
To avoid recompilation of unchanged Stan programs, we recommend calling
rstan_options(auto_write = TRUE)
For improved execution time, we recommend calling
Sys.setenv(LOCAL_CPPFLAGS = '-march=native')
although this causes Stan to throw an error on a few processors.

Attaching package: 'coda'

The following object is masked from 'package:rstan':

    traceplot



In [2]:
# add path required by rstan
library(devtools) 
Sys.setenv(PATH = paste("C:/Rtools/bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(PATH = paste("C:\\Rtools\\mingw_64\\bin", Sys.getenv("PATH"), sep=";")) 
Sys.setenv(BINPREF = "C:/Rtools/mingw_$(WIN)/bin/")

Loading required package: usethis


# Read csv into dataframe

In [3]:
dat.str <- Sys.glob("data.*.csv")
data <- as.data.frame(read.csv(file = dat.str))
# slicing training set (whole 2018 season)
dat <- data[data$period < 30,]

In [4]:
head(dat)

X   Date       Season round period home.name away.name home.score
127 145 2018-04-29 2018   6     29     FR        WC         81       
128 146 2018-04-29 2018   6     29     CW        RI         70       
129 147 2018-04-29 2018   6     29     ES        ME         72       
130 148 2018-04-28 2018   6     29     AD        GC        110       
131 149 2018-04-28 2018   6     29     HW        SK         89       
132 150 2018-04-28 2018   6     29     GW        BL         77       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
127  89        12         ... 1.9                  1.9                 
128 113        10         ... 1.9                  1.9                 
129 108        10         ... 1.9                  1.9                 
130  62        16         ... 1.9                  1.9                 
131  54        13         ... 1.9                  1.9                 
132  43        10         ... 1.9                  1.9                 
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
127 1.9                    1.9                    1.9                  
128 1.9                    1.9                    1.9                  
129 1.9                    1.9                    1.9                  
130 1.9                    1.9                    1.9                  
131 1.9                    1.9                    1.9                  
132 1.9                    1.9                    1.9                  
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
127 1.9                   1.9                            1           8         
128 1.9                   1.9                            5          12         
129 1.9                   1.9                           11          13         
130 1.9                   1.9                           17           7         
131 1.9                   1.9                           16          15         
132 1.9                   1.9                            6          10

In [5]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

In [82]:
# library(hash)

# h <- hash()

# for (i in 1:length(sort(unique(dat$home.name)))){
#     h[[as.character(sort(unique(dat$home.name))[i])]] <- i
# }

# home.number <- vector()
# away.number <- vector()

# for (i in 1:nrow(dat)){
#     home.number <- append(home.number, h[[as.character(dat$home.name[i])]])
#     away.number <- append(away.number, h[[as.character(dat$away.name[i])]])
    
# }

# dat$home.number <- home.number
# dat$away.number <- away.number

In [84]:
# write.csv(dat, 'temp.csv')

# 2019 Round 1 data

In [6]:
matchup <- data[data$period == 30,]
n.matches <- length(matchup$home.number)
matchup

X   Date       Season round period home.name away.name home.score
118 136 2018-05-06 2018   7     30     BL        CW        114       
119 137 2018-05-06 2018   7     30     SK        ME         67       
120 138 2018-05-06 2018   7     30     RI        FR        110       
121 139 2018-05-05 2018   7     30     AD        CA        125       
122 140 2018-05-05 2018   7     30     SY        NM         66       
123 141 2018-05-05 2018   7     30     WC        PA        102       
124 142 2018-05-05 2018   7     30     ES        HW         67       
125 143 2018-05-05 2018   7     30     WB        GC         81       
126 144 2018-05-04 2018   7     30     GE        GW         93       
    away.score home.goals ... Total.Score.Over.Min Total.Score.Over.Max
118 121        18         ... 1.9                  1.9                 
119 106         9         ... 1.9                  1.9                 
120  33        15         ... 1.9                  1.9                 
121  70        19         ... 1.9                  1.9                 
122  68         9         ... 1.9                  1.9                 
123  60        16         ... 1.9                  1.9                 
124  90        10         ... 1.9                  1.9                 
125  72        11         ... 1.9                  1.9                 
126  32        14         ... 1.9                  1.9                 
    Total.Score.Over.Close Total.Score.Under.Open Total.Score.Under.Min
118 1.9                    1.9                    1.9                  
119 1.9                    1.9                    1.9                  
120 1.9                    1.9                    1.9                  
121 1.9                    1.9                    1.9                  
122 1.9                    1.9                    1.9                  
123 1.9                    1.9                    1.9                  
124 1.9                    1.9                    1.9                  
125 1.9                    1.9                    1.9                  
126 1.9                    1.9                    1.9                  
    Total.Score.Under.Max Total.Score.Under.Close Notes home.number away.number
118 1.9                   1.9                           15           5         
119 1.9                   1.9                            8          10         
120 1.9                   1.9                           13          12         
121 1.9                   1.9                            7           4         
122 1.9                   1.9                            9          16         
123 1.9                   1.9                           11           1         
124 1.9                   1.9                           14           2         
125 1.9                   1.9                            3          17         
126 1.9                   1.9                            6          18

# Data

In [7]:
home.name <- as.matrix(dat$home.name)
away.name <- as.matrix(dat$away.name)
home.numb <- dat$home.number
away.numb <- dat$away.number

home.Goals <- dat$home.goals
home.Behinds <- dat$home.behinds
away.Goals <- dat$away.goals
away.Behinds <- dat$away.behinds

period <- dat$period
n.teams <- 18
n.games <- length(home.numb)
n.periods <- max(period)
n.bps <- 2
bps <- c(1,24)

In [8]:
# matricies for the Owen paper centering
ones <- matrix(1, nrow = (n.teams-1), ncol = 1)
S_t <-  n.teams / (n.teams-1) * (diag(n.teams-1) + ones %*% t(ones))

# Jmat is n * n-1
J.up.left <- diag(n.teams-1) - (1/n.teams)*(ones %*% t(ones))
J.bot.left <- - t(ones) * 1/n.teams

Jmat <- rbind(J.up.left, J.bot.left)

# Store data into list required by STAN

In [9]:
dat.list <- list(N = n.teams,
                 G = n.games,
                 T = n.periods,
                 period = period,
                 home = home.numb,
                 away = away.numb,
                 homeGoals = home.Goals,
                 homeBehinds = home.Behinds,
                 awayGoals = away.Goals,
                 awayBehinds = away.Behinds,
                 BP = n.bps,
                 Breaks = bps,
                 Smat = S_t,
                 JmatTrans = t(Jmat),
                 N_Matches = n.matches,
                 nextHome = matchup$home.number,
                 nextAway = matchup$away.number)

# Compile the model

In [10]:
prefit <- stan("Skellam goal and behind difference.stan", data = dat.list, chains = 0)

DIAGNOSTIC(S) FROM PARSER:
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: assignment operator <- deprecated in the Stan language; use = instead.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # are deprecated.  Please use // in place of # for line comments.
Info: Comments beginning with # 

the number of chains is less than 1; sampling not done


# Sampling using MCMC (4 cores in parallel)

In [11]:
cl <- makeCluster(4)

clusterEvalQ(cl, library(rstan))

myfunction <- function(var1, var2, var3){
    stan(fit = var3, data = var2,
                            chains = 1, chain_id = var1, iter = 2500,
                            refresh = -1, init = "0")
}

sflist <- parLapply(cl, 1:4, fun = myfunction, var2 = dat.list, var3 = prefit)
stopCluster(cl)

[[1]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[2]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[3]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"       

[[4]]
 [1] "rstan"       "ggplot2"     "StanHeaders" "stats"       "graphics"   
 [6] "grDevices"   "utils"       "datasets"    "methods"     "base"

In [11]:
sflist

[[1]]
Inference for Stan model: Skellam goal and behind difference.
1 chains, each with iter=2500; warmup=1250; thin=1; 
post-warmup draws per chain=1250, total post-warmup draws=1250.

                           mean se_mean     sd   2.5%    25%    50%    75%
delta                      0.65    0.00   0.07   0.51   0.61   0.66   0.70
attackGoals_raw[1,1]       1.91    0.10   2.54  -3.27   0.21   2.10   3.70
attackGoals_raw[1,2]      -4.70    0.11   2.77  -8.87  -6.93  -5.00  -2.70
attackGoals_raw[1,3]      -3.54    0.12   3.32  -8.79  -6.17  -3.85  -1.09
attackGoals_raw[1,4]      -0.07    0.12   3.10  -6.24  -2.22  -0.04   2.04
attackGoals_raw[1,5]       0.51    0.11   2.64  -4.56  -1.24   0.44   2.21
attackGoals_raw[1,6]       1.01    0.10   2.79  -4.61  -0.93   1.11   2.93
attackGoals_raw[1,7]      -0.10    0.10   2.57  -5.12  -1.84  -0.10   1.54
attackGoals_raw[1,8]       1.38    0.13   2.66  -3.90  -0.50   1.42   3.27
attackGoals_raw[1,9]       1.37    0.06   1.92  -2.32   0.09   1

In [12]:
fit <- sflist2stanfit(sflist)

In [13]:
write.csv(print(summary(fit)), file = "fitproper.csv")

$summary
                                  mean      se_mean           sd          2.5%
delta                     9.112909e-01 0.0012072583 6.454770e-02   0.787489160
attackGoals_raw[1,1]      2.050937e+00 0.0702815883 2.636854e+00  -3.026181257
attackGoals_raw[1,2]     -1.503099e+00 0.0704888107 3.340000e+00  -7.774595139
attackGoals_raw[1,3]      1.422164e+00 0.0696130929 2.999336e+00  -4.703584829
attackGoals_raw[1,4]     -2.207403e+00 0.0628638164 2.805199e+00  -7.399341772
attackGoals_raw[1,5]      1.213100e+00 0.0681580514 3.249916e+00  -5.539156400
attackGoals_raw[1,6]      9.566901e-01 0.0615949894 2.951412e+00  -4.796767399
attackGoals_raw[1,7]      1.180569e+00 0.0629935138 2.934869e+00  -4.535460107
attackGoals_raw[1,8]     -1.113067e-01 0.0545098336 2.810598e+00  -5.623704202
attackGoals_raw[1,9]      7.576936e-02 0.0817981859 3.236995e+00  -6.432056209
attackGoals_raw[1,10]    -3.069573e+00 0.0638769812 3.334549e+00  -8.574390215
attackGoals_raw[1,11]     1.855410e+00 0.06

# Extract parameters

In [14]:
fit.samples <- extract(fit)
write.csv(fit.samples, file = "samples.csv")

# Take the average of the mu for each team

In [15]:
# parameter estimate extractor
delta <- mean (fit.samples$delta)
muAttGoals.vec <- apply(fit.samples$muAttGoals, 2, mean) # I think the 18th team here is
  # suffering from the sum to zero constraint, maybe will dissapear with more samples

muAttBehinds.vec <- apply(fit.samples$muAttBehinds, 2, mean)
muDef.vec <- apply(fit.samples$muDef, 2, mean)

mu.ests <- matrix(c( "Goal attack mean estimates", muAttGoals.vec,"Behind attack mean estimates", muAttBehinds.vec,
                     "defend means estimates", muDef.vec), ncol = 3, byrow = F)
write.csv(mu.ests, file = "AR mean estimates.csv")

# Extract phiAtt, phiDef, attackGoals, attackBehinds, defend

In [16]:
phiAtt.vec <- mean(fit.samples$phiAtt)
phiDef.vec <- mean(fit.samples$phiDef)
std.attack.vec <- mean(fit.samples$stdAtt)
std.def.vec <- mean(fit.samples$stdDef)

goal.attack.strenghts.mat <- apply(fit.samples$attackGoals, 2:3, mean)
write.csv(goal.attack.strenghts.mat, file = "goal.attack.str.csv")

behind.attack.strengths.mat <- apply(fit.samples$attackBehinds, 2:3, mean)
write.csv(behind.attack.strengths.mat, file = "behind.attack.str.csv")

defence.strengths.mat <- apply(fit.samples$defend, 2:3, mean)
write.csv(defence.strengths.mat, file = "def.str.csv")

par.vec <- c(delta, "delta",
             phiAtt.vec, "phi.attack",
             phiDef.vec, "phi.defend",
             std.attack.vec, "std.attack",
             std.def.vec, "std.defend")

par.vec.est <- matrix(par.vec, ncol = 2, byrow = T)
write.csv(par.vec.est,  file = "parameter estimates.csv")

# Extract goalDiff, behindDiff, and totalDiff

In [17]:
avg.pred.goal.diff <- apply(fit.samples$goalDiff, 2, mean)
avg.pred.behind.diff <- apply(fit.samples$behindDiff, 2, mean)
avg.pred.total.diff <- apply(fit.samples$totalDiff, 2, mean)

In [18]:
# see if we got it right
actual.total.diff <- matchup$home.score - matchup$away.score
correct.vec <- ((avg.pred.total.diff * actual.total.diff)>0)

In [19]:
actual.total.diff
correct.vec

[1]  -7 -39  77  55  -2  42 -23   9  61

[1] FALSE FALSE  TRUE  TRUE FALSE  TRUE  TRUE  TRUE  TRUE

# Calculate percentage of win, loss and draw

In [20]:
# get the percentage of win/loss

winDrawLossPer <- function(x.vec) {
  home.win.per <- mean(as.numeric(x.vec > 0))
  draw.per <- mean(as.numeric(x.vec == 0))
  away.win.per <- mean(as.numeric(x.vec < 0))
  c(home.win.per, draw.per ,away.win.per)
}

In [21]:
per.chance.mat <- apply(fit.samples$totalDiff, 2, winDrawLossPer)
per.chance.mat

iterations [,1]   [,2]   [,3]   [,4]   [,5]  [,6]   [,7]   [,8]   [,9]  
      [1,] 0.9106 0.9504 0.9308 0.8730 0.862 0.8184 0.2542 0.5252 0.7660
      [2,] 0.0088 0.0124 0.0182 0.0122 0.020 0.0250 0.0374 0.0290 0.0682
      [3,] 0.0806 0.0372 0.0510 0.1148 0.118 0.1566 0.7084 0.4458 0.1658

In [22]:
# the sd ests are going to be wildly larger than they should due to not throwing out burn in
# samples, should probably change all my apply's to deal with this but ehhhhhhhh, more samples
# takes care of it for the most part
sd.ests <- round(apply(fit.samples$totalDiff,2,sd),2)

In [23]:
sim.pred.mat <- matrix(c("behind diff", avg.pred.behind.diff,
                         "goal diff", avg.pred.goal.diff,
                         "total diff", avg.pred.total.diff,
                         "home team", as.character(matchup$home.name),
                         "away team", as.character(matchup$away.name),
                         "actual result", actual.total.diff,
                         "prediction correct?", correct.vec,
                         "home win prob", per.chance.mat[1,],
                         "draw prob", per.chance.mat[2,],
                         "home loss prob", per.chance.mat[3,],
                         "simulated sd ests", sd.ests
                         ), nrow = 11, byrow = T)

write.csv(sim.pred.mat, file = "internal predictions.csv")

In [24]:
sim.pred.mat

[,1]                [,2]    [,3]    [,4]    [,5]    [,6]    [,7]   
 [1,] behind diff         13.5558 10.1874 3.0016  9.3962  6.1884  3.9594 
 [2,] goal diff           9.5262  6.8962  11.8386 10.5638 8.4484  4.9648 
 [3,] total diff          70.713  51.5646 74.0332 72.779  56.8788 33.7482
 [4,] home team           BL      SK      RI      AD      SY      WC     
 [5,] away team           CW      ME      FR      CA      NM      PA     
 [6,] actual result       -7      -39     77      55      -2      42     
 [7,] prediction correct? FALSE   FALSE   TRUE    TRUE    FALSE   TRUE   
 [8,] home win prob       0.9106  0.9504  0.9308  0.873   0.862   0.8184 
 [9,] draw prob           0.0088  0.0124  0.0182  0.0122  0.02    0.025  
[10,] home loss prob      0.0806  0.0372  0.051   0.1148  0.118   0.1566 
[11,] simulated sd ests   102.85  64.44   107.13  110.61  87.57   67.85  
      [,8]     [,9]   [,10]  
 [1,] -1.6022  2.7184 1.5076 
 [2,] -2.1142  0.9374 2.8188 
 [3,] -14.2874 8.3428 18.4204
 [4,] ES       WB     GE     
 [5,] HW       GC     GW     
 [6,] -23      9      61     
 [7,] TRUE     TRUE   TRUE   
 [8,] 0.2542   0.5252 0.766  
 [9,] 0.0374   0.029  0.0682 
[10,] 0.7084   0.4458 0.1658 
[11,] 38.9     49.05  30.62

In [25]:
write.csv(t(sim.pred.mat),  file = "round7_prediction.csv")